---------------------------------------------------------------------------------------------------------

In [1]:
!pip install lightning

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 811.0/811.0 kB 21.7 MB/s eta 0:00:00


In [2]:
import os
import time
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import random_split, DataLoader
import torchvision.datasets as datasets
from torchvision import transforms
from torchvision.models import vit_b_16, ViT_B_16_Weights, resnet50, ResNet50_Weights
from lightning import LightningModule, Trainer, LightningDataModule
from lightning.pytorch.callbacks import ModelCheckpoint
from lightning.pytorch.utilities import rank_zero_info

# Set environment variable to handle CUDA memory fragmentation
os.environ['PYTORCH_CUDA_ALLOC_CONF'] = 'max_split_size_mb:128'

# Ensure that GPU usage is maximized
torch.backends.cudnn.benchmark = True
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Define dataset path
dir0 = '/kaggle/input/cirrus-cumulus-stratus-nimbus-ccsn-database/CCSN_v2'

class DataModule(LightningDataModule):
    def __init__(self, transform, batch_size=32, num_workers=4):
        super().__init__()
        self.root_dir = dir0
        self.transform = transform
        self.batch_size = batch_size
        self.num_workers = num_workers

    def setup(self, stage=None):
        dataset = datasets.ImageFolder(root=self.root_dir, transform=self.transform)
        self.class_names = dataset.classes
        n_data = len(dataset)
        n_train = int(0.7 * n_data)
        n_val = int(0.15 * n_data)
        n_test = n_data - n_train - n_val
        self.train_dataset, self.val_dataset, self.test_dataset = random_split(dataset, [n_train, n_val, n_test])

    def train_dataloader(self):
        return DataLoader(self.train_dataset, batch_size=self.batch_size, shuffle=True, num_workers=self.num_workers, pin_memory=True)

    def val_dataloader(self):
        return DataLoader(self.val_dataset, batch_size=self.batch_size, num_workers=self.num_workers, pin_memory=True)

    def test_dataloader(self):
        return DataLoader(self.test_dataset, batch_size=self.batch_size, num_workers=self.num_workers, pin_memory=True)

class VisionTransformer(LightningModule):
    def __init__(self, class_names):
        super(VisionTransformer, self).__init__()
        self.model = vit_b_16(weights=ViT_B_16_Weights.IMAGENET1K_V1)
        self.model.heads.head = nn.Linear(self.model.heads.head.in_features, len(class_names))

    def forward(self, X):
        X = self.model(X)
        return F.log_softmax(X, dim=1)

    def training_step(self, batch, batch_idx):
        X, y = batch
        y_hat = self(X)
        loss = F.cross_entropy(y_hat, y)
        self.log("train_loss", loss)
        return loss

    def validation_step(self, batch, batch_idx):
        X, y = batch
        y_hat = self(X)
        loss = F.cross_entropy(y_hat, y)
        acc = (y_hat.argmax(dim=1) == y).float().mean()
        self.log("val_loss", loss)
        self.log("val_acc", acc)

    def test_step(self, batch, batch_idx):
        X, y = batch
        y_hat = self(X)
        loss = F.cross_entropy(y_hat, y)
        acc = (y_hat.argmax(dim=1) == y).float().mean()
        self.log("test_loss", loss)
        self.log("test_acc", acc)

    def configure_optimizers(self):
        optimizer = torch.optim.AdamW(self.parameters(), lr=0.0001)
        lr_scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
        return {'optimizer': optimizer, 'lr_scheduler': lr_scheduler}

class ResNet(LightningModule):
    def __init__(self, class_names):
        super(ResNet, self).__init__()
        self.model = resnet50(weights=ResNet50_Weights.IMAGENET1K_V2)
        self.model.fc = nn.Linear(self.model.fc.in_features, len(class_names))

    def forward(self, X):
        X = self.model(X)
        return F.log_softmax(X, dim=1)

    def training_step(self, batch, batch_idx):
        X, y = batch
        y_hat = self(X)
        loss = F.cross_entropy(y_hat, y)
        self.log("train_loss", loss)
        return loss

    def validation_step(self, batch, batch_idx):
        X, y = batch
        y_hat = self(X)
        loss = F.cross_entropy(y_hat, y)
        acc = (y_hat.argmax(dim=1) == y).float().mean()
        self.log("val_loss", loss)
        self.log("val_acc", acc)

    def test_step(self, batch, batch_idx):
        X, y = batch
        y_hat = self(X)
        loss = F.cross_entropy(y_hat, y)
        acc = (y_hat.argmax(dim=1) == y).float().mean()
        self.log("test_loss", loss)
        self.log("test_acc", acc)

    def configure_optimizers(self):
        optimizer = torch.optim.AdamW(self.parameters(), lr=0.0001)
        lr_scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
        return {'optimizer': optimizer, 'lr_scheduler': lr_scheduler}

def clear_gpu_memory():
    torch.cuda.empty_cache()
    torch.cuda.reset_peak_memory_stats()

def eta_callback(epoch_idx, total_epochs, epoch_start_time):
    elapsed_time = time.time() - epoch_start_time
    remaining_time = elapsed_time * (total_epochs - epoch_idx - 1)
    eta = time.strftime("%H:%M:%S", time.gmtime(remaining_time))
    print(f"Epoch {epoch_idx + 1}/{total_epochs} completed. ETA: {eta}", end="\r")

def train_and_test_model(model_class, model_name, transform, device, epochs=100):
    datamodule = DataModule(transform=transform)
    datamodule.setup()
    
    model = model_class(class_names=datamodule.class_names).to(device)
    
    checkpoint_callback = ModelCheckpoint(
        monitor="val_acc",
        dirpath=f"/kaggle/working/{model_name}",
        filename=f"{model_name}" + "-{epoch:02d}-{val_acc:.2f}",
        save_top_k=1,
        mode="max"
    )
    
    trainer = Trainer(
        max_epochs=epochs,
        devices=1 if device.type == 'cuda' else None,
        accelerator="gpu" if device.type == 'cuda' else "cpu",
        log_every_n_steps=5,
        precision="16-mixed",
        callbacks=[checkpoint_callback]
    )

    for epoch_idx in range(epochs):
        epoch_start_time = time.time()
        trainer.fit(model, datamodule)
        eta_callback(epoch_idx, epochs, epoch_start_time)
    
    print("\nTesting the trained model...")
    test_results = trainer.test(model, dataloaders=datamodule.test_dataloader())

    final_model_path = f"/kaggle/working/{model_name}_final_model.pth"
    torch.save(model.state_dict(), final_model_path)
    print(f"Final model saved to: {final_model_path}")

    results_df = pd.DataFrame(test_results)
    results_path = f"/kaggle/working/{model_name}_test_results.csv"
    results_df.to_csv(results_path, index=False)
    print(f"Test results saved to: {results_path}")

    clear_gpu_memory()

if __name__ == '__main__':
    transform_with_crop = transforms.Compose([
        transforms.RandomRotation(10),
        transforms.RandomHorizontalFlip(),
        transforms.RandomVerticalFlip(),
        transforms.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.2, hue=0.1),
        transforms.Resize(224),
        transforms.CenterCrop(224),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ])

    print("Training VisionTransformer model with CenterCrop for 100 epochs...")
    train_and_test_model(VisionTransformer, "VisionTransformer_with_crop", transform_with_crop, device, epochs=300)

    print("Training ResNet50 model with CenterCrop for 100 epochs...")
    train_and_test_model(ResNet, "ResNet50_with_crop", transform_with_crop, device, epochs=1)


Training VisionTransformer model with CenterCrop for 100 epochs...


Downloading: "https://download.pytorch.org/models/vit_b_16-c867db91.pth" to /root/.cache/torch/hub/checkpoints/vit_b_16-c867db91.pth
100%|██████████| 330M/330M [00:02<00:00, 156MB/s]
INFO: Using 16bit Automatic Mixed Precision (AMP)
INFO: GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
2024-08-29 22:17:43.303509: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-08-29 22:17:43.303647: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-08-29 22:17:43.430631: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registere

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

/opt/conda/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


Training: |          | 0/? [00:00<?, ?it/s]

...

INFO: `Trainer.fit` stopped: `max_epochs=1` reached.
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Epoch 1/1 completed. ETA: 00:00:00
Testing the trained model...


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│         test_acc          │    0.4005235731601715     │
│         test_loss         │    1.8834757804870605     │
└───────────────────────────┴───────────────────────────┘

Final model saved to: /kaggle/working/ResNet50_with_crop_final_model.pth
Test results saved to: /kaggle/working/ResNet50_with_crop_test_results.csv
